In [1]:
# 8) Deep Learning
#     a) Build a  DNN with five hidden layers of 100 neurons
#     each, He initialization, 
#     and the ELU activation function.
    
#     b) Using the Adam optimization and early stopping, 
#     try training it on MNIST but only on digits 0 to 4,
#     as we will use transfer learning for digits 5 to 9
#     in the next exercise. You will need a 
#     softmax output layer with 5 neurons, 
#     and as always make sure to 
#     save checkpoints at regular intervals and save 
#     the final model so you can reuse it later.


In [2]:
from __future__ import absolute_import, division, print_function, unicode_literals

import tensorflow as tf
import numpy as np
from sklearn.model_selection import GridSearchCV

In [3]:
(X_train, y_train), (X_test, y_test) = tf.keras.datasets.mnist.load_data()

In [4]:
X_train, X_test = X_train / 255.0, X_test / 255.0

In [5]:
X_train_0_to_4, y_train_0_to_4 = X_train[y_train <= 4], y_train[y_train <= 4]

X_test_0_to_4, y_test_0_to_4 = X_test[y_test <= 4], y_test[y_test <= 4]

In [6]:
def create_model():
    he_initializer = tf.keras.initializers.he_normal(seed=None)

    model = tf.keras.models.Sequential([
        tf.keras.layers.Flatten(input_shape=(28, 28)),
        tf.keras.layers.Dense(100, activation='elu', kernel_initializer=he_initializer),
        tf.keras.layers.Dense(100, activation='elu', kernel_initializer=he_initializer),
        tf.keras.layers.Dense(100, activation='elu', kernel_initializer=he_initializer),
        tf.keras.layers.Dense(100, activation='elu', kernel_initializer=he_initializer),
        tf.keras.layers.Dense(100, activation='elu', kernel_initializer=he_initializer),
        tf.keras.layers.Dropout(0.2),
        tf.keras.layers.Dense(5, activation='softmax')    
    ])

    model.compile(optimizer='adam', 
                  loss='sparse_categorical_crossentropy', 
                  metrics=['accuracy'])
    return model

In [7]:
import os
checkpoint_path = "training_0_4/cp.ckpt"
checkpoint_dir = os.path.dirname(checkpoint_path)

In [8]:
cp_callback = tf.keras.callbacks.ModelCheckpoint(filepath=checkpoint_path,
                                                 save_weights_only=True,
                                                 verbose=1)

In [213]:
early_stopping = tf.keras.callbacks.EarlyStopping(monitor='loss', min_delta=0, patience=20, verbose=2)

In [36]:
model = tf.keras.wrappers.scikit_learn.KerasClassifier(build_fn=create_model)
# model = create_model()

# Applying Grid Search from scikit-learn
# https://machinelearningmastery.com/grid-search-hyperparameters-deep-learning-models-python-keras/

In [ ]:
# START HERE

In [35]:
param_grid = dict(epochs=[10, 20, 30], batch_size=[10, 20, 40])
grid = GridSearchCV(estimator=model, param_grid=param_grid, cv=3, error_score='raise', verbose=2)

grid_result = grid.fit(X_train_0_to_4, y_train_0_to_4)

Fitting 3 folds for each of 9 candidates, totalling 27 fits
[CV] batch_size=10, epochs=10 ........................................


[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.


Train on 20397 samples
Epoch 1/10
 6200/20397 [========>.....................] - ETA: 7s - loss: 0.2861 - accuracy: 0.9155

KeyboardInterrupt: 

In [69]:
model = tf.keras.wrappers.scikit_learn.KerasClassifier(build_fn=create_model)
model.fit(X_train_0_to_4, y_train_0_to_4, **best_params, callbacks=[early_stopping], validation_data=(X_test_0_to_4,y_test_0_to_4))

Train on 30596 samples, validate on 5139 samples
Epoch 1/30
30596/30596 [==============================] - 5s 155us/sample - loss: 0.1235 - accuracy: 0.9615 - val_loss: 0.1057 - val_accuracy: 0.9673
Epoch 2/30
30596/30596 [==============================] - 3s 104us/sample - loss: 0.0570 - accuracy: 0.9825 - val_loss: 0.0510 - val_accuracy: 0.9860
Epoch 3/30
30596/30596 [==============================] - 6s 192us/sample - loss: 0.0434 - accuracy: 0.9862 - val_loss: 0.0368 - val_accuracy: 0.9875
Epoch 4/30
30596/30596 [==============================] - 3s 107us/sample - loss: 0.0346 - accuracy: 0.9893 - val_loss: 0.0305 - val_accuracy: 0.9907
Epoch 5/30
30596/30596 [==============================] - 3s 94us/sample - loss: 0.0259 - accuracy: 0.9916 - val_loss: 0.0310 - val_accuracy: 0.9899
Epoch 6/30
30596/30596 [==============================] - 3s 90us/sample - loss: 0.0247 - accuracy: 0.9926 - val_loss: 0.0371 - val_accuracy: 0.9905
Epoch 7/30
30596/30596 [=============================

In [38]:
def create_model_with_batch_norm():
    he_initializer = tf.keras.initializers.he_normal(seed=None)

    model = tf.keras.models.Sequential([
        tf.keras.layers.Flatten(input_shape=(28, 28)),
        tf.keras.layers.BatchNormalization(axis=-1, momentum=0.99, epsilon=0.001, center=True, scale=True),
        tf.keras.layers.Dense(100, activation='elu', kernel_initializer=he_initializer),
        tf.keras.layers.Dense(100, activation='elu', kernel_initializer=he_initializer),
        tf.keras.layers.Dense(100, activation='elu', kernel_initializer=he_initializer),
        tf.keras.layers.Dense(100, activation='elu', kernel_initializer=he_initializer),
        tf.keras.layers.Dense(100, activation='elu', kernel_initializer=he_initializer),
        tf.keras.layers.Dropout(0.2),
        tf.keras.layers.Dense(5, activation='softmax')    
    ])

    model.compile(optimizer='adam', 
                  loss='sparse_categorical_crossentropy', 
                  metrics=['accuracy'])
    return model


In [67]:
model_bn = tf.keras.wrappers.scikit_learn.KerasClassifier(build_fn=create_model_with_batch_norm)


In [68]:
model_bn.fit(X_train_0_to_4, y_train_0_to_4, **best_params, callbacks=[early_stopping], validation_data=(X_test_0_to_4,y_test_0_to_4))

Train on 30596 samples, validate on 5139 samples
Epoch 1/30
30596/30596 [==============================] - 7s 242us/sample - loss: 0.1298 - accuracy: 0.9611 - val_loss: 0.0478 - val_accuracy: 0.9842
Epoch 2/30
30596/30596 [==============================] - 5s 178us/sample - loss: 0.0577 - accuracy: 0.9824 - val_loss: 0.0469 - val_accuracy: 0.9862
Epoch 3/30
30596/30596 [==============================] - 4s 145us/sample - loss: 0.0405 - accuracy: 0.9877 - val_loss: 0.0509 - val_accuracy: 0.9862
Epoch 4/30
30596/30596 [==============================] - 5s 164us/sample - loss: 0.0337 - accuracy: 0.9894 - val_loss: 0.0540 - val_accuracy: 0.9866
Epoch 5/30
30596/30596 [==============================] - 7s 233us/sample - loss: 0.0282 - accuracy: 0.9910 - val_loss: 0.0529 - val_accuracy: 0.9858
Epoch 6/30
30596/30596 [==============================] - 6s 182us/sample - loss: 0.0267 - accuracy: 0.9918 - val_loss: 0.0451 - val_accuracy: 0.9875
Epoch 7/30
30596/30596 [===========================

In [23]:
param_grid = dict(epochs=[10, 20, 30], batch_size=[10, 20, 40])
grid = GridSearchCV(estimator=model, param_grid=param_grid, cv=3, error_score='raise', verbose=2)

grid_result = grid.fit(X_train_0_to_4, y_train_0_to_4)

Fitting 3 folds for each of 9 candidates, totalling 27 fits
[CV] batch_size=10, epochs=10 ........................................


[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.


Train on 20397 samples
Epoch 1/10
20397/20397 [==============================] - 7s 338us/sample - loss: 0.2008 - accuracy: 0.9410
Epoch 2/10
20397/20397 [==============================] - 6s 285us/sample - loss: 0.1081 - accuracy: 0.9681
Epoch 3/10
20397/20397 [==============================] - 6s 284us/sample - loss: 0.0949 - accuracy: 0.9731
Epoch 4/10
20397/20397 [==============================] - 6s 291us/sample - loss: 0.0786 - accuracy: 0.9770
Epoch 5/10
20397/20397 [==============================] - 6s 289us/sample - loss: 0.0675 - accuracy: 0.9793
Epoch 6/10
20397/20397 [==============================] - 6s 283us/sample - loss: 0.0582 - accuracy: 0.9817
Epoch 7/10
20397/20397 [==============================] - 6s 286us/sample - loss: 0.0606 - accuracy: 0.9820 - loss: 0.061
Epoch 8/10
20397/20397 [==============================] - 6s 286us/sample - loss: 0.0524 - accuracy: 0.9848
Epoch 9/10
20397/20397 [==============================] - 6s 288us/sample - loss: 0.0420 - accuracy

[CV] ......................... batch_size=10, epochs=10, total= 1.0min
[CV] batch_size=10, epochs=10 ........................................


[Parallel(n_jobs=1)]: Done   1 out of   1 | elapsed:  1.0min remaining:    0.0s


...

[CV] ......................... batch_size=40, epochs=30, total= 2.0min
[CV] batch_size=40, epochs=30 ........................................
Train on 20397 samples
Epoch 1/30
20397/20397 [==============================] - 4s 179us/sample - loss: 0.1433 - accuracy: 0.9568
Epoch 2/30
20397/20397 [==============================] - 2s 111us/sample - loss: 0.0615 - accuracy: 0.9808
Epoch 3/30
20397/20397 [==============================] - 2s 114us/sample - loss: 0.0453 - accuracy: 0.9859
Epoch 4/30
20397/20397 [==============================] - 2s 112us/sample - loss: 0.0370 - accuracy: 0.9883
Epoch 5/30
20397/20397 [==============================] - 2s 116us/sample - loss: 0.0279 - accuracy: 0.9910
Epoch 6/30
20397/20397 [==============================] - 2s 113us/sample - loss: 0.0242 - accuracy: 0.9930
Epoch 7/30
20397/20397 [==============================] - 2s 116us/sample - loss: 0.0240 - accuracy: 0.9929
Epoch 8/30
20397/20397 [==============================] - 3s 128us/sample - los

[CV] ......................... batch_size=40, epochs=30, total= 1.2min
[CV] batch_size=40, epochs=30 ........................................
Train on 20398 samples
Epoch 1/30
20398/20398 [==============================] - 3s 138us/sample - loss: 0.1541 - accuracy: 0.9544
Epoch 2/30
20398/20398 [==============================] - 2s 108us/sample - loss: 0.0648 - accuracy: 0.9796
Epoch 3/30
20398/20398 [==============================] - 2s 108us/sample - loss: 0.0495 - accuracy: 0.9846
Epoch 4/30
20398/20398 [==============================] - 2s 111us/sample - loss: 0.0331 - accuracy: 0.9891
Epoch 5/30
20398/20398 [==============================] - 2s 108us/sample - loss: 0.0305 - accuracy: 0.9900
Epoch 6/30
20398/20398 [==============================] - 2s 106us/sample - loss: 0.0328 - accuracy: 0.9889
Epoch 7/30
20398/20398 [==============================] - 2s 106us/sample - loss: 0.0202 - accuracy: 0.9934
Epoch 8/30
20398/20398 [==============================] - 2s 104us/sample - los

[CV] ......................... batch_size=40, epochs=30, total= 1.2min


[Parallel(n_jobs=1)]: Done  27 out of  27 | elapsed: 537.3min finished


Train on 30596 samples
Epoch 1/30
30596/30596 [==============================] - 4s 135us/sample - loss: 0.1271 - accuracy: 0.9611
Epoch 2/30
30596/30596 [==============================] - 4s 115us/sample - loss: 0.0558 - accuracy: 0.9835
Epoch 3/30
30596/30596 [==============================] - 3s 111us/sample - loss: 0.0411 - accuracy: 0.9873
Epoch 4/30
30596/30596 [==============================] - 3s 112us/sample - loss: 0.0323 - accuracy: 0.9902
Epoch 5/30
30596/30596 [==============================] - 3s 111us/sample - loss: 0.0271 - accuracy: 0.9910
Epoch 6/30
30596/30596 [==============================] - 3s 111us/sample - loss: 0.0270 - accuracy: 0.9917
Epoch 7/30
30596/30596 [==============================] - 3s 110us/sample - loss: 0.0219 - accuracy: 0.9932
Epoch 8/30
30596/30596 [==============================] - 3s 112us/sample - loss: 0.0194 - accuracy: 0.9943
Epoch 9/30
30596/30596 [==============================] - 3s 108us/sample - loss: 0.0190 - accuracy: 0.9944
Epoch

In [49]:
best_params = grid_result.best_params_

In [50]:
best_params

{'batch_size': 40, 'epochs': 30}

In [ ]:
grid_bn = create_model_bn

In [ ]:
# Run grid search on model_bn, take best params and use those to compare model and model_bn
# Don't bother running GridSearch on model for now

In [51]:
model.fit(X_train_0_to_4, y_train_0_to_4, callbacks=[early_stopping], validation_data=(X_test_0_to_4,y_test_0_to_4))

Train on 30596 samples, validate on 5139 samples
30596/30596 [==============================] - 5s 154us/sample - loss: 0.1182 - accuracy: 0.9645 - val_loss: 0.0540 - val_accuracy: 0.9829


In [47]:
model_bn.fit(X_train_0_to_4, y_train_0_to_4, callbacks=[early_stopping], validation_data=(X_test_0_to_4,y_test_0_to_4))

Train on 30596 samples, validate on 5139 samples
30596/30596 [==============================] - 5s 171us/sample - loss: 0.1313 - accuracy: 0.9612 - val_loss: 0.0559 - val_accuracy: 0.9842


In [ ]:
# TODO: add 5-9
def create_model_():
    he_initializer = tf.keras.initializers.he_normal(seed=None)

    model = tf.keras.models.Sequential([
        tf.keras.layers.Flatten(input_shape=(28, 28)),
        tf.keras.layers.Dense(100, activation='elu', kernel_initializer=he_initializer),
        tf.keras.layers.Dense(100, activation='elu', kernel_initializer=he_initializer),
        tf.keras.layers.Dense(100, activation='elu', kernel_initializer=he_initializer),
        tf.keras.layers.Dense(100, activation='elu', kernel_initializer=he_initializer),
        tf.keras.layers.Dense(100, activation='elu', kernel_initializer=he_initializer),
        tf.keras.layers.Dropout(0.2),
        tf.keras.layers.Dense(5, activation='softmax')    
    ])

    model.compile(optimizer='adam', 
                  loss='sparse_categorical_crossentropy', 
                  metrics=['accuracy'])
    return model

In [ ]:
############################

In [52]:
def create_model_with_batch_norm_and_dropout():
    he_initializer = tf.keras.initializers.he_normal(seed=None)

    model = tf.keras.models.Sequential([
        tf.keras.layers.Flatten(input_shape=(28, 28)),
        tf.keras.layers.BatchNormalization(axis=-1, momentum=0.99, epsilon=0.001, center=True, scale=True),
        tf.keras.layers.Dense(100, activation='elu', kernel_initializer=he_initializer),
        tf.keras.layers.Dropout(0.2),
        tf.keras.layers.Dense(100, activation='elu', kernel_initializer=he_initializer),
        tf.keras.layers.Dropout(0.2),
        tf.keras.layers.Dense(100, activation='elu', kernel_initializer=he_initializer),
        tf.keras.layers.Dropout(0.2),
        tf.keras.layers.Dense(100, activation='elu', kernel_initializer=he_initializer),
        tf.keras.layers.Dropout(0.2),
        tf.keras.layers.Dense(100, activation='elu', kernel_initializer=he_initializer),
        tf.keras.layers.Dropout(0.2),
        tf.keras.layers.Dense(5, activation='softmax')    
    ])

    model.compile(optimizer='adam', 
                  loss='sparse_categorical_crossentropy', 
                  metrics=['accuracy'])
    return model


In [53]:
def create_model_with_dropout():
    he_initializer = tf.keras.initializers.he_normal(seed=None)

    model = tf.keras.models.Sequential([
        tf.keras.layers.Flatten(input_shape=(28, 28)),
        tf.keras.layers.BatchNormalization(axis=-1, momentum=0.99, epsilon=0.001, center=True, scale=True),
        tf.keras.layers.Dense(100, activation='elu', kernel_initializer=he_initializer),
        tf.keras.layers.Dropout(0.2),
        tf.keras.layers.Dense(100, activation='elu', kernel_initializer=he_initializer),
        tf.keras.layers.Dropout(0.2),
        tf.keras.layers.Dense(100, activation='elu', kernel_initializer=he_initializer),
        tf.keras.layers.Dropout(0.2),
        tf.keras.layers.Dense(100, activation='elu', kernel_initializer=he_initializer),
        tf.keras.layers.Dropout(0.2),
        tf.keras.layers.Dense(100, activation='elu', kernel_initializer=he_initializer),
        tf.keras.layers.Dropout(0.2),
        tf.keras.layers.Dense(5, activation='softmax')    
    ])

    model.compile(optimizer='adam', 
                  loss='sparse_categorical_crossentropy', 
                  metrics=['accuracy'])
    return model


In [64]:
model_bn_do = create_model_with_batch_norm_and_dropout()
model_bn_do_result = model_bn_do.fit(X_train_0_to_4, y_train_0_to_4, epochs=30, batch_size=40, callbacks=[early_stopping], validation_data=(X_test_0_to_4,y_test_0_to_4))

Train on 30596 samples, validate on 5139 samples
Epoch 1/30
30596/30596 [==============================] - 5s 166us/sample - loss: 0.2733 - accuracy: 0.9241 - val_loss: 0.0656 - val_accuracy: 0.9833
Epoch 2/30
30596/30596 [==============================] - 4s 131us/sample - loss: 0.1227 - accuracy: 0.9636 - val_loss: 0.0487 - val_accuracy: 0.9850
Epoch 3/30
30596/30596 [==============================] - 4s 132us/sample - loss: 0.0887 - accuracy: 0.9744 - val_loss: 0.0453 - val_accuracy: 0.9887
Epoch 4/30
30596/30596 [==============================] - 4s 131us/sample - loss: 0.0737 - accuracy: 0.9788 - val_loss: 0.0437 - val_accuracy: 0.9891
Epoch 5/30
30596/30596 [==============================] - 4s 128us/sample - loss: 0.0621 - accuracy: 0.9812 - val_loss: 0.0468 - val_accuracy: 0.9868
Epoch 6/30
30596/30596 [==============================] - 4s 131us/sample - loss: 0.0559 - accuracy: 0.9841 - val_loss: 0.0468 - val_accuracy: 0.9868
Epoch 7/30
30596/30596 [===========================

In [76]:
model_bn_do_result.history.keys()

dict_keys(['loss', 'accuracy', 'val_loss', 'val_accuracy'])

In [84]:
model_bn_do_result.history['val_accuracy']

[0.9832652,
 0.9850165,
 0.98871374,
 0.98910296,
 0.9867678,
 0.9867678,
 0.98910296,
 0.9898813,
 0.98890835,
 0.9900759,
 0.9918272,
 0.99143803,
 0.99143803,
 0.99085426,
 0.99241096,
 0.99065965,
 0.9922164,
 0.99085426,
 0.99260557,
 0.99065965,
 0.9912434,
 0.9918272,
 0.9896867,
 0.9920218,
 0.9918272,
 0.99338394,
 0.99338394,
 0.99260557,
 0.98910296,
 0.99416226]

In [60]:
model_do = create_model_with_dropout()
model_do_result = model_do.fit(X_train_0_to_4, y_train_0_to_4, epochs=30, batch_size=40, callbacks=[early_stopping], validation_data=(X_test_0_to_4,y_test_0_to_4))

Train on 30596 samples, validate on 5139 samples
Epoch 1/30
30596/30596 [==============================] - 6s 204us/sample - loss: 0.2576 - accuracy: 0.9262 - val_loss: 0.0634 - val_accuracy: 0.9811
Epoch 2/30
30596/30596 [==============================] - 4s 126us/sample - loss: 0.1204 - accuracy: 0.9647 - val_loss: 0.0577 - val_accuracy: 0.9848
Epoch 3/30
30596/30596 [==============================] - 6s 205us/sample - loss: 0.0849 - accuracy: 0.9746 - val_loss: 0.0444 - val_accuracy: 0.9872
Epoch 4/30
30596/30596 [==============================] - 4s 147us/sample - loss: 0.0764 - accuracy: 0.9777 - val_loss: 0.0414 - val_accuracy: 0.9877
Epoch 5/30
30596/30596 [==============================] - 4s 132us/sample - loss: 0.0587 - accuracy: 0.9831 - val_loss: 0.0474 - val_accuracy: 0.9891
Epoch 6/30
30596/30596 [==============================] - 4s 129us/sample - loss: 0.0516 - accuracy: 0.9850 - val_loss: 0.0361 - val_accuracy: 0.9901
Epoch 7/30
30596/30596 [===========================

In [ ]:
############################

In [ ]:
# 11.9 Transfer Learning

In [ ]:
############################

In [111]:
# 11.9.A) Create new DNN and add pretrained hidden layers from model_bn_do

In [110]:
from tensorflow.keras import layers

In [85]:
model_bn_do.summary()

Model: "sequential_58"
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
flatten_58 (Flatten)         (None, 784)               0         
_________________________________________________________________
batch_normalization_46 (Batc (None, 784)               3136      
_________________________________________________________________
dense_348 (Dense)            (None, 100)               78500     
_________________________________________________________________
dropout_86 (Dropout)         (None, 100)               0         
_________________________________________________________________
dense_349 (Dense)            (None, 100)               10100     
_________________________________________________________________
dropout_87 (Dropout)         (None, 100)               0         
_________________________________________________________________
dense_350 (Dense)            (None, 100)             

In [105]:
new_model = tf.keras.models.Sequential()

In [107]:
# https://stackoverflow.com/questions/55335228/how-to-remove-the-last-layer-from-a-pre-trained-model-i-have-tried-model-layers
# Add all layers except softmax layer (output layer)

for layer in model_bn_do.layers[:-1]:
    new_model.add(layer)

In [112]:
# Freeze the layers
for layer in new_model.layers:
    layer.trainable = False

In [114]:
# Add new softmax layer with 10 output nodes
new_model.add(layers.Dense(10, activation='softmax'))

In [115]:
new_model.summary()

Model: "sequential_65"
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
flatten_58 (Flatten)         (None, 784)               0         
_________________________________________________________________
batch_normalization_46 (Batc (None, 784)               3136      
_________________________________________________________________
dense_348 (Dense)            (None, 100)               78500     
_________________________________________________________________
dropout_86 (Dropout)         (None, 100)               0         
_________________________________________________________________
dense_349 (Dense)            (None, 100)               10100     
_________________________________________________________________
dropout_87 (Dropout)         (None, 100)               0         
_________________________________________________________________
dense_350 (Dense)            (None, 100)             

In [116]:
# 11.9.B) Train new DNN on digits 5-9 using only 100 images per digit, and time how long it takes

In [117]:
X_train_5_to_9, y_train_5_to_9 = X_train[y_train >= 5], y_train[y_train >= 5]
X_test_5_to_9, y_test_5_to_9 = X_test[y_test >= 5], y_test[y_test >= 5]

In [118]:
X_train_all_5s, y_train_all_5s = X_train[y_train == 5], X_train[y_train == 5]

In [152]:
X_train_all_5s, y_train_all_5s = X_train[y_train == 5][:100], X_train[y_train == 5][:100]
len(X_train_all_5s)

100

In [153]:
X_test_all_5s, y_test_all_5s = X_test[y_test == 5][:100], X_test[y_test == 5][:100]
len(X_test_all_5s)

100

In [205]:
X_train_5_to_9_100, y_train_5_to_9_100 = X_train_all_5s, y_train_all_5s

for num in range(6, 10):
    next_X_train, next_y_train = X_train[y_train == num][:100], X_train[y_train == num][:100]
    X_train_5_to_9_100 = np.concatenate((X_train_5_to_9_100, next_X_train), axis=0)
    y_train_5_to_9_100 = np.concatenate((y_train_5_to_9_100, next_y_train))
    
print('total length X: ', X_train_5_to_9_100.shape)
print('total length y: ', y_train_5_to_9_100.shape)

total length X:  (500, 28, 28)
total length y:  (500, 28, 28)


In [210]:
X_test_5_to_9_100, y_test_5_to_9_100 = X_test_all_5s, y_test_all_5s

for num in range(6, 10):
    next_X_test, next_y_test = X_test[y_test == num][:100], X_test[y_test == num][:100]
    X_test_5_to_9_100 = np.concatenate((X_test_5_to_9_100, next_X_test), axis=0)
    y_test_5_to_9_100 = np.concatenate((y_test_5_to_9_100, next_y_test))
    
print('total length X: ', X_test_5_to_9_100.shape)
print('total length y: ', y_test_5_to_9_100.shape)
print('type y: ', type(y_test_5_to_9_100))

total length X:  (500, 28, 28)
total length y:  (500, 28, 28)
type y:  <class 'numpy.ndarray'>


In [209]:
print('total length X: ', X_test_0_to_4.shape)
print('total length y: ', y_test_0_to_4.shape)
print('type y: ', type(y_test_0_to_4))

total length X:  (5139, 28, 28)
total length y:  (5139,)
type y:  <class 'numpy.ndarray'>


In [195]:
new_model.compile(optimizer='adam', 
              loss='sparse_categorical_crossentropy', 
              metrics=['accuracy'])

In [199]:
# new_model.summary()

In [215]:
new_model.fit(X_train_5_to_9, y_train_5_to_9, epochs=50, batch_size=40, validation_data=(X_test_5_to_9, y_test_5_to_9))

Train on 29404 samples, validate on 4861 samples
Epoch 1/50
29404/29404 [==============================] - 3s 113us/sample - loss: 1.1948 - accuracy: 0.5519 - val_loss: 1.0357 - val_accuracy: 0.5943
Epoch 2/50
29404/29404 [==============================] - 5s 158us/sample - loss: 1.1994 - accuracy: 0.5535 - val_loss: 1.0025 - val_accuracy: 0.6579
Epoch 3/50
29404/29404 [==============================] - 4s 141us/sample - loss: 1.2014 - accuracy: 0.5502 - val_loss: 1.0466 - val_accuracy: 0.6147
Epoch 4/50
29404/29404 [==============================] - 3s 105us/sample - loss: 1.1931 - accuracy: 0.5533 - val_loss: 1.0167 - val_accuracy: 0.6392
Epoch 5/50
29404/29404 [==============================] - 7s 248us/sample - loss: 1.1903 - accuracy: 0.5550 - val_loss: 1.0023 - val_accuracy: 0.6406
Epoch 6/50
29404/29404 [==============================] - 6s 219us/sample - loss: 1.1932 - accuracy: 0.5571 - val_loss: 1.0266 - val_accuracy: 0.6219
Epoch 7/50
29404/29404 [===========================

In [174]:
print(y_train_0_to_4.shape)
print(y_train_5_to_9_100.shape)

()
(28, 28)


In [178]:
# X_train_0_to_4, y_train_0_to_4 = X_train[y_train <= 4], y_train[y_train <= 4]
y_train_0_to_4.shape

(30596,)

In [217]:
# 11.9.C) Try caching the frozen layers, and train the model again: how much faster is it now?

In [229]:
cached_frozen_model = tf.keras.models.Sequential()
cached_frozen_model.add(new_model)

In [230]:
cached_frozen_model.summary()

Model: "sequential_69"
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
sequential_65 (Sequential)   (None, 10)                123046    
Total params: 123,046
Trainable params: 1,010
Non-trainable params: 122,036
_________________________________________________________________


In [232]:
cached_frozen_model.compile(optimizer='adam', 
                  loss='sparse_categorical_crossentropy', 
                  metrics=['accuracy'])

In [233]:
cached_frozen_model.fit(X_train_5_to_9, y_train_5_to_9, epochs=50, batch_size=40, validation_data=(X_test_5_to_9, y_test_5_to_9))

Train on 29404 samples, validate on 4861 samples
Epoch 1/50
29404/29404 [==============================] - 6s 209us/sample - loss: 1.1977 - accuracy: 0.5531 - val_loss: 0.9936 - val_accuracy: 0.6490
Epoch 2/50
29404/29404 [==============================] - 3s 94us/sample - loss: 1.1967 - accuracy: 0.5530 - val_loss: 1.0439 - val_accuracy: 0.6100
Epoch 3/50
29404/29404 [==============================] - 4s 124us/sample - loss: 1.1953 - accuracy: 0.5534 - val_loss: 0.9978 - val_accuracy: 0.6441
Epoch 4/50
29404/29404 [==============================] - 3s 97us/sample - loss: 1.1839 - accuracy: 0.5585 - val_loss: 1.0114 - val_accuracy: 0.6338
Epoch 5/50
29404/29404 [==============================] - 4s 127us/sample - loss: 1.1940 - accuracy: 0.5508 - val_loss: 0.9934 - val_accuracy: 0.6488
Epoch 6/50
29404/29404 [==============================] - 4s 120us/sample - loss: 1.1978 - accuracy: 0.5547 - val_loss: 0.9999 - val_accuracy: 0.6431
Epoch 7/50
29404/29404 [=============================